# Quantum Circuit Design through Monte Carlo Tree Search
In this tutorial we are going to show the whole pipeline of the Monte Carlo Tree Search (MCTS) implemented for quantum circuit design.

## Brief intro to the task of quantum circuit design
The goal is finding a quantum circuit that solve a certain problem.  
What is a quantum circuit? We show a random quantum circuit is below.

In [3]:
# Import library that allow to work with quantum circuits
from qiskit import QuantumCircuit

# Initialize a quantum circuit with 4 qubits
qc = QuantumCircuit(4)
# Add a non-parameterized gate on the 0th qubit 
qc.h(0)
# Add a parameterized gate on each of the four qubits (all with a parameter fixed to 0.5)
for i in range(4):
    qc.ry(0.5, i)
print("You have built your first quantum circuit:")
qc.draw()

# If you want to print the circuit in a fancier way uncomment replace the previous line of code with the following one
# qc.draw("mpl")

You have built your first quantum circuit:


┌───┐   ┌─────────┐
q_0: ───┤ H ├───┤ Ry(0.5) ├
     ┌──┴───┴──┐└─────────┘
q_1: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_2: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_3: ┤ Ry(0.5) ├───────────
     └─────────┘

Designing a quantum circuit means finding the ordered sequence of gates (parameterized and not-parameterized) applied to the qubits that give raise to the circuit that can solve the given problem.
You can imagine the task of designing a quantum circuit as the quantum analogue of the design of Neural Networks. In neural networks you have to find the stucture (number of neurons, hidden layers, activation function, etc.) that allows to solve the problem after the learning of the parameters (weights). In quantum circuit, we also have to find the structure (sequence of gates), that allows to solve the problem after the learning of the parameters (angle parameters of the parameterized gates).
However the search space defined by quantum circuits is extremely big and we want to find automatic and efficient way to get "good" circuit. Namely, we want a shallow circuit that evaluated on the objevtive function gives a value close to the optimum.

In this project, we will provide you some problems encoded in the circuit-based quantum computing setting in a black-box form. That means, that the problems are provided as real-valued function on the domain of quantum circuits. This functions will be your objective functions and your goal is to minimize them.

You don't have to understand what exactly those "quantum" functions do, but you only need to work with MCTS and its variants to get hopefully better results (lower values of the objective functions).

## Objective functions


Here we define an objective function to optimize. The objective function is a real-valued function defined on quantum circuits. You can find examples in the field of quantum chemistry, systems of linear equations, combinatorial optimizatio (Max-Cut) in the file evaluation_functions.py. 

Let's take as example the a famous example from the domain of quantum chemistry. In order to study molecule is important to estimate their ground state energy. We are going to use an hybrid classical-quantum algorithm, the variational quantum eigensolver, to estimate the ground state energy of the hydrogen molecule $H_2$. In the following we evaluate the quantum circuit created above as a solution for this specific problem.

You can change the problem as described above, the number of qubits required for each problem is in the dictionary named "N_QUBITS" in file main.py

In [4]:

import evaluation_functions as evf

problem = evf.h2
# You can equivalently work with the other evaluation functions (pay attention the number of qubits required depends on the evaluation function):
"""
# Quantum Chemistry But on different molecules
problem = evf.lih
problem = evf.h2o
# Different systems of linear equations
problem = evf.vqls_0
problem = evf.vqls_1
# NP-Hard problem: MAX-CUT
problem = evf.max_cut

"""
cost_value = problem(qc, cost=True)

print(f"Given the quantum circuit below: \n{qc}\n the objective function returns: {cost_value}")

Given the quantum circuit below: 
        ┌───┐   ┌─────────┐
q_0: ───┤ H ├───┤ Ry(0.5) ├
     ┌──┴───┴──┐└─────────┘
q_1: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_2: ┤ Ry(0.5) ├───────────
     ├─────────┤           
q_3: ┤ Ry(0.5) ├───────────
     └─────────┘           
 the objective function returns: -0.2318460796537938


## Link Quantum to Classical
Once we have defined the problem, we can use MCTS in order to design a first guess, also known as "ansatz", for the initial quantum circuit that.
We hope you did not get scared with this brief intro into the "quantum world". Anyways, from now on you will only work with classical techniques. Here there is the link we created between the classical and quantum "world":
- Node: Quantum Circuit
- Moves: apply changes to the circuit. There are 4 possible changes implemented:
    1. Add new random gate in random position
    2. Remove radom gate in random position
    3. Swap a random gate with a new gate in the same position
    4. Change the angle parameter in a parameterized gate
- Objective function: quantum black box provided


    


## Your MCTS baseline
Below you will see how does your baseline work

In [5]:
# Number of qubits required by the problem. In the problem of estimating the ground state energy of the ydrogen we only need 4 qubits (For all the other problems we provide you of all the information)
variable_qubits = 4
ancilla_qubits = 0
# Max depth of the circuit that we want to search with the MCTS
max_depth = 10
# Computational budget we provide MCTS to explore the search space. it is equivalent to the number of new nodes evaluated
budget = 1000
# Set to false MCTS use an adaptive technique to fix the branching factor of each node. This allows to explore more the most promising nodes. Set to an integer, the branching factor will be fixed for all nodes of the tree.
branches = False

criteria = "average_value"
rollout_type = 'classic'
roll_out_steps = 2
choices = {'a': 50, 'd': 10, 's': 20, 'c': 20, 'p': 0}
epsilon = None
stop_deterministic = False
# Hyperparametrs of MCTS
ucb = 0.4
pw_C = 1
pw_alpha = 0.3


Below we define the root node by inizializing an empty circuit. The search starts from that node and MCTS will search for the best.

In [6]:
import mcts
from structure import Circuit
# Initialize the search by creating an empty circuit in the root node
root = mcts.Node(Circuit(variable_qubits=variable_qubits, ancilla_qubits=ancilla_qubits), max_depth=max_depth)
        
best_path = mcts.mcts(root, budget=budget, branches=branches, evaluation_function=problem, criteria=criteria, rollout_type=rollout_type, roll_out_steps=roll_out_steps,
                                choices=choices, epsilon=epsilon, stop_deterministic=stop_deterministic, ucb_value=ucb, pw_C=pw_C, pw_alpha=pw_alpha, verbose=True)

Root Node:
 Tree depth: 0  -  Generated by Action: None  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐
v_0: ┤ H ├
     ├───┤
v_1: ┤ H ├
     ├───┤
v_2: ┤ H ├
     ├───┤
v_3: ┤ H ├
     └───┘
Epoch Counter:  0
Node Expanded:
 Tree depth: 1  -  Generated by Action: a  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐┌───────────┐
v_0: ┤ H ├┤ Ry(3.971) ├
     ├───┤└───────────┘
v_1: ┤ H ├─────────────
     ├───┤             
v_2: ┤ H ├─────────────
     ├───┤             
v_3: ┤ H ├─────────────
     └───┘             
Reward:  -0.4105175203641639
Epoch Counter:  1
Node Expanded:
 Tree depth: 1  -  Generated by Action: a  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐┌────────────┐
v_0: ┤ H ├┤ Rz(3.4524) ├
     ├───┤└────────────┘
v_1: ┤ H ├──────────────
     ├───┤              
v_2: ┤ H ├──────────────
     ├───┤              

Finally it outputs the path that creates the best circuit, starting from the root to the leaf. In the following we print the values of the objective function evaluated on the quantum circuits designed along the best path. Note that, in this formulation, a children node is not necessarily better than the parent.
Remember that this is a minimization problem and the lower the objective value the better the node

In [7]:
quantum_circuit_path = best_path['qc']
cost = []
for i in range(len(quantum_circuit_path)):
    cost.append(problem(quantum_circuit_path[i], cost=True))
    print("Node at depth tree: ", i, "number of children: ", best_path["children"][i])
    print("Objective value: ", cost[i])
    print("Cumulative Reward: ", best_path["value"][i])
    print("Average Reward: ", best_path["value"][i]/best_path["visits"][i], "\n")

Node at depth tree:  0 number of children:  4
Objective value:  -0.04207897977473338
Cumulative Reward:  289.8335187696279
Average Reward:  0.28954397479483307 

Node at depth tree:  1 number of children:  4
Objective value:  -0.04207897977473342
Cumulative Reward:  291.565663313972
Average Reward:  0.2999646741913292 

Node at depth tree:  2 number of children:  4
Objective value:  -0.04207897977473342
Cumulative Reward:  291.11646498702146
Average Reward:  0.31102186430237333 

Node at depth tree:  3 number of children:  4
Objective value:  -0.04207897977473338
Cumulative Reward:  289.33108553863957
Average Reward:  0.3225541644800887 

Node at depth tree:  4 number of children:  4
Objective value:  -0.1748601043030764
Cumulative Reward:  285.1588288574641
Average Reward:  0.3296633859623862 

Node at depth tree:  5 number of children:  4
Objective value:  -0.5428901884916151
Cumulative Reward:  279.0063645952365
Average Reward:  0.3377801024155406 

Node at depth tree:  6 number of 

At this poit we selct the ansatz as the best quantum circuit found in the path.

In [8]:
ansatz = quantum_circuit_path[cost.index(min(cost))]
print("Selected Ansatz: \n", ansatz)

Selected Ansatz: 
           ┌───┐     ┌─────────────┐                                 
v_0: ─────┤ H ├─────┤ Rz(0.19734) ├─────────────────────────────────
          ├───┤     └┬────────────┤┌────────────┐                   
v_1: ─────┤ H ├──────┤ Rx(2.6667) ├┤ Ry(2.2978) ├──■────────────────
     ┌────┴───┴────┐ └────────────┘└────────────┘  │                
v_2: ┤ Rz(0.15988) ├───────────────────────────────┼────────────────
     └────┬───┬────┘ ┌────────────┐              ┌─┴─┐┌────────────┐
v_3: ─────┤ H ├──────┤ Rx(5.9249) ├──────────────┤ X ├┤ Ry(4.2536) ├
          └───┘      └────────────┘              └───┘└────────────┘


## Parameter Optimization
Once we designed the structure of our quantum circuit we optimize the parameters through a classical gradient-based optimizer. Here we chose the ADAM Optimizer

In [9]:
problem(quantum_circuit=ansatz, gradient=True)

Step = 0,  Energy = -0.68854406 Ha
Step = 2,  Energy = -0.69583192 Ha
Step = 4,  Energy = -0.70293786 Ha
Step = 6,  Energy = -0.70985127 Ha
Step = 8,  Energy = -0.71656197 Ha
Step = 10,  Energy = -0.72306043 Ha
Step = 12,  Energy = -0.72933786 Ha
Step = 14,  Energy = -0.73538637 Ha
Step = 16,  Energy = -0.74119908 Ha
Step = 18,  Energy = -0.74677021 Ha
Step = 20,  Energy = -0.75209519 Ha
Step = 22,  Energy = -0.75717072 Ha
Step = 24,  Energy = -0.76199481 Ha
Step = 26,  Energy = -0.76656681 Ha
Step = 28,  Energy = -0.77088744 Ha
Step = 30,  Energy = -0.77495873 Ha
Step = 32,  Energy = -0.77878397 Ha
Step = 34,  Energy = -0.78236770 Ha
Step = 36,  Energy = -0.78571559 Ha
Step = 38,  Energy = -0.78883432 Ha
Step = 40,  Energy = -0.79173152 Ha
Step = 42,  Energy = -0.79441556 Ha
Step = 44,  Energy = -0.79689550 Ha
Step = 46,  Energy = -0.79918086 Ha
Step = 48,  Energy = -0.80128153 Ha
Step = 50,  Energy = -0.80320762 Ha
Step = 52,  Energy = -0.80496931 Ha
Step = 54,  Energy = -0.80657674 

[array(-0.68483534),
 array(-0.68854406),
 array(-0.69221005),
 array(-0.69583192),
 array(-0.6994083),
 array(-0.70293786),
 array(-0.70641928),
 array(-0.70985127),
 array(-0.71323257),
 array(-0.71656197),
 array(-0.7198383),
 array(-0.72306043),
 array(-0.72622729),
 array(-0.72933786),
 array(-0.73239119),
 array(-0.73538637),
 array(-0.73832259),
 array(-0.74119908),
 array(-0.74401516),
 array(-0.74677021),
 array(-0.74946371),
 array(-0.75209519),
 array(-0.75466429),
 array(-0.75717072),
 array(-0.75961426),
 array(-0.76199481),
 array(-0.76431231),
 array(-0.76656681),
 array(-0.76875846),
 array(-0.77088744),
 array(-0.77295408),
 array(-0.77495873),
 array(-0.77690185),
 array(-0.77878397),
 array(-0.78060569),
 array(-0.7823677),
 array(-0.78407073),
 array(-0.78571559),
 array(-0.78730314),
 array(-0.78883432),
 array(-0.7903101),
 array(-0.79173152),
 array(-0.79309963),
 array(-0.79441556),
 array(-0.79568046),
 array(-0.7968955),
 array(-0.79806189),
 array(-0.79918086